In [3]:
import pandas as pd
# Load the dataset using pandas
dataset_path = 'dataset/disease.csv'
df = pd.read_csv(dataset_path)


In [4]:
df

Disease Fever Cough Fatigue Difficulty Breathing  Age  Gender  \
0      Influenza   Yes    No     Yes                  Yes   19  Female   
1    Common Cold    No   Yes     Yes                   No   25  Female   
2         Eczema    No   Yes     Yes                   No   25  Female   
3         Asthma   Yes   Yes      No                  Yes   25    Male   
4         Asthma   Yes   Yes      No                  Yes   25    Male   
..           ...   ...   ...     ...                  ...  ...     ...   
344       Stroke   Yes    No     Yes                   No   80  Female   
345       Stroke   Yes    No     Yes                   No   85    Male   
346       Stroke   Yes    No     Yes                   No   85    Male   
347       Stroke   Yes    No     Yes                   No   90  Female   
348       Stroke   Yes    No     Yes                   No   90  Female   

    Blood Pressure Cholesterol Level Outcome Variable  
0              Low            Normal         Positive  
1           Normal            Normal         Negative  
2           Normal            Normal         Negative  
3           Normal            Normal         Positive  
4           Normal            Normal         Positive  
..             ...               ...              ...  
344           High              High         Positive  
345           High              High         Positive  
346           High              High         Positive  
347           High              High         Positive  
348           High              High         Positive  

[349 rows x 10 columns]

In [11]:
from typing import Optional
from mistralai import Mistral
import json
from pydantic import BaseModel

class Response(BaseModel):
    question: Optional[str] = None
    report: Optional[dict] = None


class ChatBot:
    def __init__(self, api_key, history=None):
        self.api_key = api_key
        self.history = history if history is not None else [
            {
                "role": "system",
                "content": """
You are a medical assistant chatbot responsible for triaging patients as they arrive and generating a concise report to aid the doctor in prioritizing care.
On every user input you have the history of your past responses and the patient's responses.

# Instructions:
1. Ask up to five questions to quickly understand the patient's: 
    - main complaint.
    - the duration and progression of symptoms.
    - pain or discomfort level.
    - presence of any severe symptoms (such as chest pain or difficulty breathing).
    - presence of any other symptoms (such as fever, cough, or fatigue).
    - relevant medical background (medications, conditions).

2. Create a brief, clear report based on the patient’s responses, highlighting the key information that indicates the urgency of their condition.

# Constraints:
- ask only one question at a time.
- ask easy questions that a sick person can answer.
- be empathetic and professional.
- ask up to five questions.
- generate a concise report when you are done.
- dont add ```json ```  chars in the response.

# Output Format:
- Response format: JSON
    - when you want to ask a question, generate a JSON object with the key "question" and the value as the question you want to ask.
    - when you are done asking questions, generate a report with the key "report" and the value as this schema:
        - "main_complaint": "string"
        - "duration": "string"
        - "progression": "string"
        - "pain_level": "string"
        - "severe_symptoms": "string"
        - "other_symptoms": "string"
        - "medical_background"
        - "emergency_level": "string"
- No additional text, spaces, or explanations should be included.
- your response should match this pydantic schema:
        """,
            }
        ]
        self.client = Mistral(api_key=api_key)
        self.model = "mistral-large-latest"

    def get_response(self, question):
        chat_response = self.client.chat.complete(
            model=self.model,
            messages=self.history + [{"role": "user", "content": question}],
            response_format = {
                "type": "json_object",
            }
        )

        self.history.append({"role": "user", "content": question})

        bot_message = chat_response.choices[0].message
        self.history.append({"role": bot_message.role, "content": bot_message.content})

        return json.loads(bot_message.content)


In [12]:
api_key = "POVQ5Fl6l3k7ODsPuNjSgJwAxr3Svqmz"  

chatbot = ChatBot(api_key)

question = "I need help; I'm having severe chest pain and can barely breathe."
question = "I need help; I'm having headaches and disiness."
answer = chatbot.get_response(question)
print(f"Q: {question}\nA: {answer}")

Q: I need help; I'm having headaches and disiness.
A: {'question': 'Can you describe your main complaint for me?'}


In [92]:
import streamlit as st

def main():
    st.title("Medical Assistant Chatbot")
    st.write("Whats your medical problem?")


    chatbot = ChatBot(api_key)
    user_input = st.text_input("You:", "")

    end = False
    while not end:
        if st.button("Send"):
            if user_input:
                response = chatbot.get_response(user_input)
                if "question" in response:
                    st.write("Chatbot:", response["question"])
                    user_input = st.text_input("You:", "")
                elif "report" in response:
                    st.write("Chatbot:", response["report"])
                    end = True

if __name__ == "__main__":
    main()


2024-10-12 19:20:34.053 WARNING streamlit.runtime.scriptrunner_utils.script_run_context: Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2024-10-12 19:20:34.173 
  command:

    streamlit run /Users/mohamedlahdir/workspace/mistral-alan-hackathon/.venv/lib/python3.11/site-packages/ipykernel_launcher.py [ARGUMENTS]
2024-10-12 19:20:34.174 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2024-10-12 19:20:34.175 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2024-10-12 19:20:34.175 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2024-10-12 19:20:34.175 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2024-10-12 19:20:34.176 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2

KeyboardInterrupt: 

In [91]:
question = "no"
answer = chatbot.get_response(question)
print(f"Q: {question}\nA: {answer}")

Q: no
A: {'report': {'main_complaint': 'Headaches and dizziness', 'duration': 'Last 2 hours', 'progression': 'Not specified', 'pain_level': '7 out of 10', 'severe_symptoms': 'Fast heartbeat', 'other_symptoms': 'None specified', 'medical_background': 'Not specified', 'emergency_level': 'High'}}


In [46]:
chatbot.history

[{'role': 'system',
  'content': '\nYou are a medical assistant chatbot responsible for triaging patients as they arrive and generating a concise report to aid the doctor in prioritizing care.\nOn every user input you have the history of your past responses and the patient\'s responses.\n\n# Instructions:\n1. Ask up to five questions to quickly understand the patient\'s main complaint, the duration and progression of symptoms, pain or discomfort level, presence of any severe symptoms (such as chest pain or difficulty breathing), and relevant medical background (medications, conditions).\n2. Create a brief, clear report based on the patient’s responses, highlighting the key information that indicates the urgency of their condition.\n\n# Constraints:\n- ask only one question at a time.\n- ask easy questions that a sick person can answer.\n- be empathetic and professional.\n- ask up to five questions.\n- generate a concise report when you are done.\n\n# Output Format:\n- Response format: 

In [20]:
chatbot.history

[{'role': 'system',
  'content': '\nYou are a medical assistant chatbot responsible for triaging patients as they arrive and generating a concise report to aid the doctor in prioritizing care. Your primary tasks are to:\n\n# Instructions:\n1. Ask up to five questions to quickly understand the patient\'s main complaint, the duration and progression of symptoms, pain or discomfort level, presence of any severe symptoms (such as chest pain or difficulty breathing), and relevant medical background (medications, conditions).\n2. Create a brief, clear report based on the patient’s responses, highlighting the key information that indicates the urgency of their condition.\n\n# Constraints:\n- ask only one question at a time.\n- ask easy questions that a sick person can answer.\n- be empathetic and professional.\n- ask up to five questions.\n- generate a concise report when you are done.\n\n# Output Format:\n- Response format: JSON\n    - when you want to ask question generate a json object wit

In [ ]:

question = "What its population?"
answer = chatbot.get_response(question)
print(f"Q: {question}\nA: {answer}")


print("Conversation History:")
for entry in chatbot.history:
    print(f"{entry['role']}: {entry['content']}")

In [ ]:

# Extract relevant data from the dataset to use as context
# Assuming the dataset has columns like 'Disease', 'Symptoms', 'Profile', etc.
# We will extract this information for a specific disease
disease_name = "diabetes"  # You can change this to another disease
disease_data = df[df['Disease'] == disease_name]

# Create context from the dataset: extracting symptoms and patient profiles
if not disease_data.empty:
    symptoms = disease_data['Symptoms'].values[0]  # Get the symptoms for the disease
    profile = disease_data['Profile'].values[0]    # Get the patient profile info for the disease
    
    # Format the context for Mistral
    context = f"Disease: {disease_name}\nSymptoms: {symptoms}\nPatient Profile: {profile}"
else:
    context = f"No data available for the disease: {disease_name}"

# Define the Mistral prompt with the extracted context
mistral_prompt = f"Based on the following medical data, generate key diagnostic questions for a doctor to ask a patient to pre-classify the disease:\n\n{context}\n\nKPIs:"

# Make the API call to Mistral to generate diagnostic questions
chat_response = client.chat.complete(
    model=model,
    messages=[
        {
            "role": "user",
            "content": mistral_prompt,
        },
    ]
)

# Print the response from Mistral (the generated KPIs)
print(chat_response.choices[0].message.content)
